In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt

import itertools


from statsmodels.tsa.stattools import grangercausalitytests, coint
from statsmodels.tsa.vector_ar.vecm import coint_johansen
from statsmodels.stats.outliers_influence import variance_inflation_factor

# estacionarieidad
from statsmodels.tsa.stattools import adfuller
from statsmodels.tsa.api import VAR

# test durbin watson
from statsmodels.stats.stattools import durbin_watson

In [2]:
df = pd.read_excel("../Datos/Acciones.xlsx",sheet_name=0)
df_prepandemia = df[df["PERIODO"]<="2020-03-01"]
df_pandemia = df[df["PERIODO"]>"2020-03-01"]

In [3]:
print(df_prepandemia.shape,df_pandemia.shape)

(1329, 80) (475, 80)


In [4]:
class Portafolio:

    INDICES = ["76_CHL_IGPA_INDICE","77_COL_COLCAP_INDICE","78_MEX_IPC_INDICE","79_PER_LIMA GENER_INDICE"]
    PERIODO = ["PERIODO"]

    def __init__(self,df):
        self.df = df
        self.tickers_info_full = self.df.columns.to_list()
        self.tickers_info_full.remove("PERIODO")
        [self.tickers_info_full.remove(indice) for indice in Portafolio.INDICES]
        self.df_final = self.df[self.tickers_info_full]
        self.test = 'ssr_chi2test'
        self.inside = False
        self.lista_results = {}
    
    def create_df_tickers(self,list_tickers,inside=False):
        tickers_info_df = pd.DataFrame(list_tickers, columns = ["column_id"])
        if inside:
            value_pais=2
        else:
            value_pais=1
        tickers_info_df["pais"] = tickers_info_df["column_id"].apply(lambda x: x.split("_")[value_pais])
        self.tickers_info_df = tickers_info_df

    def permutations_tickers(self, *args, **kwargs):
        s = list(itertools.product(*args, **kwargs))
        ids = dict()

        if self.inside:
            value_pais = 2
        else:
            value_pais = 1

        for id in s:
            value_1 = id[0].split("_")[value_pais]
            value_2 = id[1].split("_")[value_pais]
            if value_1==value_2:
                ids[id] = 1 # mismo pais
            else:
                ids[id] = 0

        ids_filters = [id for id in ids if ids[id] == 0]
        self.ids_filters = ids_filters
        
    def analysis_df(self,par_var):
        lista = Portafolio.PERIODO.copy()
        lista.extend(par_var)
        new_df = self.df.copy()
        new_df = new_df[lista]
        new_df = new_df.set_index("PERIODO")
        return new_df

    def transform_df(self,df,type_transform=None,remove_na=None):
        
        df_edit = df.copy()
        new_columns_org = df_edit.columns.tolist()

        if type_transform=="returns":            
            new_columns = ["returns_"+column for column in new_columns_org]

            for column in new_columns:
                df_edit[column] = np.log(df_edit[column.replace("returns_","")]).diff()
        
        elif type_transform=="diff":
            new_columns = ["diff_"+column for column in new_columns_org]

            for column in new_columns:
                df_edit[column] = df_edit[column.replace("diff_","")].diff()

        if type_transform:
            df_edit.drop(new_columns_org,axis=1,inplace=True)
        
        # calidad de la salida
        print("Nas:",df_edit.isna().sum())

        if remove_na:
            df_edit.dropna(inplace=True,axis=0)
            print("Correccion")
            print("Nas:",df_edit.isna().sum())

        self.inside = True
        self.apply_all(inside=True,df=df_edit.columns.tolist())
        
        return df_edit
         
    def apply_all(self,inside=False,df=None):

        if inside:
            self.create_df_tickers(list_tickers=df,inside=True)
        
        else:
            self.create_df_tickers(list_tickers=self.tickers_info_full)
        
        self.permutations_tickers(self.tickers_info_df["column_id"],repeat=2)

In [5]:
class Modelado(Portafolio):
    
    def adfuller_test_results(self,b):
        # pruebas de estacionarieidad para todas las series
        results_adftest = {}
        for column in b.columns.tolist():
            print(column)
            adf = adfuller(b[column])
            results_adftest[column] = adf[1]

        vals = np.fromiter(results_adftest.values(), dtype=float)

        return pd.DataFrame(results_adftest.items(), columns=["Ticker","p-value"])
    
    def var_model_results(self,b,max_iters):
        models_results_by_lags = {}
        model = VAR(b)
        iters = np.arange(1,max_iters)
        for i in iters:
            result = model.fit(i)
            models_results_by_lags[i] = {"aic":result.aic,
                                "bic":result.bic,
                                'fpe': result.fpe,
                                'hqic':result.hqic}
        
        # list_AIC = self.iter_var("AIC",max_iters,models_results_by_lags)
        # list_BIC = self.iter_var("BIC",max_iters,models_results_by_lags)
        # list_FPE = self.iter_var("FPE",max_iters,models_results_by_lags)
        # list_HQIC = self.iter_var("HQIC",max_iters,models_results_by_lags)

        # return (list_AIC,list_BIC,list_FPE,list_HQIC)
        return models_results_by_lags

    def durbin_watson_df(self):
        out = durbin_watson(self.results.resid)
        df_out = pd.DataFrame(out, columns={"result"})
        df_out["no_correlation"] = df_out["result"].apply(lambda x: x>1.85 and x<2.15)
        return df_out

    # def grangers_causation_matrix(self, data):    
    #     salida = pd.DataFrame(Portafolio.ids_filters, columns = ["var1","var2"])
    #     salida["p-value"] = np.nan

    #     for id,pair in enumerate(Portafolio.ids_filters):
    #         test_result = grangercausalitytests(data[list(pair)], maxlag=[self.maxlag], verbose=False) # remover parentesis en maxlag
    #         # p_values = [round(test_result[i+1][0][test][1],4) for i in range(maxlag)]     
    #         p_values = round(test_result[self.maxlag][0][self.test][1],4)
    #         # min_p_value = np.min(p_values)
    #         # salida.iloc[id,2] = min_p_value
    #         salida.iloc[id,2] = p_values
    #     return salida

    def iter_var(self,criterio,max_lag,models_results_by_lags):
        salida = [models_results_by_lags[id][criterio] for id in np.arange(1,max_lag)]
        max_lag = salida.index(min(salida))+1
        print(f"{criterio}: ",max_lag)
        return max_lag
    
    def clean_output_model(self,df):
        final_df = df.copy()
        final_df["pass_test"] = final_df["p-value"]<0.05
        final_df = final_df[final_df["pass_test"]==True]
        return final_df    
        
        
    def apply_model(self,df,max_iters,use_file_criteria=False):
        if use_file_criteria:
            new_df = pd.read_csv("modelos_info_criteria.csv")
            if list(new_df.columns)[0] == "Unnamed: 0":
                new_df.drop(["Unnamed: 0"],axis=1,inplace=True)

        else:
            model = [self.var_model_results(df[list(column)],max_iters) for column in self.ids_filters]
            print("termine modelos")
            new_df = pd.DataFrame(self.ids_filters,columns=["var1","var2"])
            new_df["aic"] = [self.iter_var("aic",max_iters,model_iter) for model_iter in model]
            print("termine AIC")
            new_df["bic"] = [self.iter_var("bic",max_iters,model_iter) for model_iter in model]
            print("termine BIC")
            new_df["fpe"] = [self.iter_var("fpe",max_iters,model_iter) for model_iter in model]
            print("termine FPE")
            new_df["hqic"] = [self.iter_var("hqic",max_iters,model_iter) for model_iter in model]
            print("termine HQIC")

            # Escritura de archivo
            new_df.to_csv("modelos_info_criteria.csv",index=False)

        return new_df
    
    def modelito(self,df,df_transform):

        modelos_lista = {}
        for row in np.arange(0,df.shape[0]):
            s = df_transform[[df.loc[row,"var1"],df.loc[row,"var2"]]]
            model = VAR(s)
            modelos_lista[row] = model
        
        self.modelos_lista = modelos_lista
    
    def criteria_selection_codition(self,df):

        criterio_a = df['aic']
        criterio_b = df['bic']
        criterio_c = df["fpe"]

        if (df['aic'] == criterio_a) & (df['bic'] == criterio_a) & (df['fpe'] == criterio_a) & (df["hqic"] == criterio_a):
            return criterio_a,"aic"
        
        elif (df['aic'] == criterio_a) & (df['fpe'] == criterio_a):
            return criterio_a,"aic"
        
        elif (df['hqic'] == criterio_b) & (df['bic'] == criterio_b):
            return criterio_b,"bic"

        else:
            return criterio_c,"fpe"
    
    def apply_best_criteria(self,df):

        new_df = df.apply(self.criteria_selection_codition, axis='columns',result_type='expand')

        df = pd.concat([df,new_df],axis='columns')
        df.rename(columns = {0:"maxlags",1:"criteria"}, inplace=True)

        return df
    
    def save_fit_models(self,maxlags,criteria,index_row):
        
        model = self.modelos_lista[index_row]
        result = model.fit(maxlags=maxlags, ic= criteria)
        self.lista_results[index_row] = result
    
    def fit_models_over_best_criteria(self,result):

        norm = result.test_normality()
        pvalue_normality = norm.pvalue
        normality = pvalue_normality<0.05

        try:
            stability = result.is_stable()
        except:
            stability = "Error"

        return pvalue_normality, normality, stability
    
    def apply_vif(self,df):
        
        try:
            vif = [variance_inflation_factor(df,id) for id in np.arange(0,2)]
            collinearity_var1 = vif[0]
            collinearity_var2 = vif[1]
        
        except:
            collinearity_var1 = "Error"
            collinearity_var2 = "Error"

        return collinearity_var1,collinearity_var2
    
    def apply_vif_results(self,df,df_transform):
        
        results = []

        for row in np.arange(0,df.shape[0]):
            new_df = df_transform[[df.loc[row,"var1"],df.loc[row,"var2"]]]
            salida = self.apply_vif(new_df)
            results.append(salida)

        results = pd.DataFrame(results,columns=["collinearity_var1","collinearity_var2"])
        print(results.shape)
        print(results.isna().sum())
        df = pd.concat([df,results],axis='columns')
        return df

    def apply_test_causality(self):
        
        list_results = []
        for id in np.arange(0,len(self.lista_results)):
            try:
                model_result = self.lista_results[id]
                test = model_result.test_causality(causing=list(model_result.params.columns)[0],caused=list(model_result.params.columns)[1])
                p_value_causality = test.pvalue
                causality = p_value_causality<0.05
                list_results.append((p_value_causality,causality))
            except:
                p_value_causality = "Error"
                causality = "Error"
                list_results.append((p_value_causality,causality))
        
        results = pd.DataFrame(list_results,columns=["p_value_causality","causality"])

        return results

    def row_name(self,df):
        df["index_row"] = df.apply(lambda x: x.name, axis='columns')
        return df

    def apply_fit(self,df):
        
        new_df = []
        # new_df = df.apply(self.fit_models_over_best_criteria, axis = 'columns', result_type='expand')
        for row in np.arange(0,len(self.lista_results)):
            result = self.lista_results[row]
            salida = self.fit_models_over_best_criteria(result)
            new_df.append(salida)

        new_df = pd.DataFrame(new_df,columns=["pvalue_normality","normality","stability"])
        df = pd.concat([df,new_df], axis='columns')

        return df

    def apply_final_model(self,df,df_transform):

        self.modelito(df,df_transform)

        # Select best criteria results
        best_model_df = self.apply_best_criteria(df)

        # Select best criteria results
        test_results = self.row_name(best_model_df)

        # Apply test results (normality,stability)
        test_results.apply(lambda x: self.save_fit_models(maxlags= x.maxlags, criteria=x.criteria, index_row= x.index_row),axis='columns')
        test_results = self.apply_fit(best_model_df)
        
        # VIF results colineality test
        test_results = self.apply_vif_results(test_results,df_transform)

        # Causality test
        causality = self.apply_test_causality()
        test_results = pd.concat([test_results,causality], axis='columns')

        return test_results
                                

# Diferencias vs Rendimientos

In [6]:
Portafolio = Modelado(df)
df_transform = Portafolio.transform_df(df=Portafolio.df_final, type_transform="returns",remove_na=True)
len(Portafolio.ids_filters)
modelos_info_criteria = Portafolio.apply_model(df_transform,max_iters=21,use_file_criteria=True) # Remover criterio adicional
test_results = Portafolio.apply_final_model(modelos_info_criteria,df_transform)
test_results.to_csv("Resuldaos_todos_modelos_full_datos.csv",index=False)

Nas: returns_1_CHL_AGUAS_SERV. P              1
returns_2_CHL_ANDINA_CONS. BAS           1
returns_3_CHL_ANTAR_ENER                 1
returns_4_CHL_BANCO CREDITO_FINAN        1
returns_5_CHL_BANCO STDER_FINAN          1
                                        ..
returns_71_PER_FERREYROS_INDUST          1
returns_72_PER_ACEROS AREQUIPA_MATER     1
returns_73_PER_EMP. SIDERURGICA_MATER    1
returns_74_PER_CASA GRANDE_CONS. BAS     1
returns_75_PER_TREVALI MINING_MATER      1
Length: 75, dtype: int64
Correccion
Nas: returns_1_CHL_AGUAS_SERV. P              0
returns_2_CHL_ANDINA_CONS. BAS           0
returns_3_CHL_ANTAR_ENER                 0
returns_4_CHL_BANCO CREDITO_FINAN        0
returns_5_CHL_BANCO STDER_FINAN          0
                                        ..
returns_71_PER_FERREYROS_INDUST          0
returns_72_PER_ACEROS AREQUIPA_MATER     0
returns_73_PER_EMP. SIDERURGICA_MATER    0
returns_74_PER_CASA GRANDE_CONS. BAS     0
returns_75_PER_TREVALI MINING_MATER      0
Length: 

d:\AnalisisAcciones\acciones\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: An unsupported index was provided and will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
d:\AnalisisAcciones\acciones\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: An unsupported index was provided and will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
d:\AnalisisAcciones\acciones\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: An unsupported index was provided and will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
d:\AnalisisAcciones\acciones\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: An unsupported index was provided and will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
d:\AnalisisAcciones\acciones\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: An unsupported index was provided and will be ignored when e.g. 

(3986, 2)
collinearity_var1    0
collinearity_var2    0
dtype: int64


In [8]:
Portafolio = Modelado(df_prepandemia)
df_transform = Portafolio.transform_df(df=Portafolio.df_final, type_transform="returns",remove_na=True)
len(Portafolio.ids_filters)
modelos_info_criteria = Portafolio.apply_model(df_transform,max_iters=21) # Remover criterio adicional
test_results = Portafolio.apply_final_model(modelos_info_criteria,df_transform)
test_results.to_csv("Resuldaos_todos_modelos_prepandemia.csv",index=False)

Nas: returns_1_CHL_AGUAS_SERV. P              1
returns_2_CHL_ANDINA_CONS. BAS           1
returns_3_CHL_ANTAR_ENER                 1
returns_4_CHL_BANCO CREDITO_FINAN        1
returns_5_CHL_BANCO STDER_FINAN          1
                                        ..
returns_71_PER_FERREYROS_INDUST          1
returns_72_PER_ACEROS AREQUIPA_MATER     1
returns_73_PER_EMP. SIDERURGICA_MATER    1
returns_74_PER_CASA GRANDE_CONS. BAS     1
returns_75_PER_TREVALI MINING_MATER      1
Length: 75, dtype: int64
Correccion
Nas: returns_1_CHL_AGUAS_SERV. P              0
returns_2_CHL_ANDINA_CONS. BAS           0
returns_3_CHL_ANTAR_ENER                 0
returns_4_CHL_BANCO CREDITO_FINAN        0
returns_5_CHL_BANCO STDER_FINAN          0
                                        ..
returns_71_PER_FERREYROS_INDUST          0
returns_72_PER_ACEROS AREQUIPA_MATER     0
returns_73_PER_EMP. SIDERURGICA_MATER    0
returns_74_PER_CASA GRANDE_CONS. BAS     0
returns_75_PER_TREVALI MINING_MATER      0
Length: 

d:\AnalisisAcciones\acciones\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: An unsupported index was provided and will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
d:\AnalisisAcciones\acciones\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: An unsupported index was provided and will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
d:\AnalisisAcciones\acciones\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: An unsupported index was provided and will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
d:\AnalisisAcciones\acciones\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: An unsupported index was provided and will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
d:\AnalisisAcciones\acciones\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: An unsupported index was provided and will be ignored when e.g. 

termine modelos
aic:  1
aic:  1
aic:  3
aic:  1
aic:  4
aic:  3
aic:  1
aic:  1
aic:  1
aic:  1
aic:  3
aic:  3
aic:  3
aic:  1
aic:  1
aic:  3
aic:  1
aic:  3
aic:  3
aic:  3
aic:  3
aic:  1
aic:  3
aic:  1
aic:  2
aic:  4
aic:  3
aic:  1
aic:  1
aic:  1
aic:  3
aic:  1
aic:  4
aic:  1
aic:  1
aic:  1
aic:  1
aic:  1
aic:  3
aic:  3
aic:  1
aic:  1
aic:  1
aic:  1
aic:  1
aic:  3
aic:  6
aic:  4
aic:  6
aic:  3
aic:  5
aic:  4
aic:  3
aic:  4
aic:  3
aic:  3
aic:  4
aic:  1
aic:  1
aic:  3
aic:  3
aic:  3
aic:  5
aic:  3
aic:  3
aic:  1
aic:  3
aic:  4
aic:  1
aic:  4
aic:  3
aic:  4
aic:  5
aic:  3
aic:  4
aic:  7
aic:  4
aic:  8
aic:  11
aic:  1
aic:  1
aic:  5
aic:  3
aic:  3
aic:  8
aic:  3
aic:  1
aic:  1
aic:  1
aic:  3
aic:  3
aic:  1
aic:  1
aic:  3
aic:  1
aic:  1
aic:  1
aic:  3
aic:  3
aic:  3
aic:  3
aic:  1
aic:  1
aic:  3
aic:  1
aic:  1
aic:  5
aic:  3
aic:  3
aic:  3
aic:  2
aic:  1
aic:  3
aic:  2
aic:  2
aic:  1
aic:  1
aic:  1
aic:  3
aic:  7
aic:  1
aic:  6
aic:  1

d:\AnalisisAcciones\acciones\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: An unsupported index was provided and will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
d:\AnalisisAcciones\acciones\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: An unsupported index was provided and will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
d:\AnalisisAcciones\acciones\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: An unsupported index was provided and will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
d:\AnalisisAcciones\acciones\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: An unsupported index was provided and will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
d:\AnalisisAcciones\acciones\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: An unsupported index was provided and will be ignored when e.g. 

(3986, 2)
collinearity_var1    0
collinearity_var2    0
dtype: int64


In [9]:
Portafolio = Modelado(df_pandemia)
df_transform = Portafolio.transform_df(df=Portafolio.df_final, type_transform="returns",remove_na=True)
len(Portafolio.ids_filters)
modelos_info_criteria = Portafolio.apply_model(df_transform,max_iters=21) # Remover criterio adicional
test_results = Portafolio.apply_final_model(modelos_info_criteria,df_transform)
test_results.to_csv("Resuldaos_todos_modelos_pandemia.csv",index=False)

Nas: returns_1_CHL_AGUAS_SERV. P              1
returns_2_CHL_ANDINA_CONS. BAS           1
returns_3_CHL_ANTAR_ENER                 1
returns_4_CHL_BANCO CREDITO_FINAN        1
returns_5_CHL_BANCO STDER_FINAN          1
                                        ..
returns_71_PER_FERREYROS_INDUST          1
returns_72_PER_ACEROS AREQUIPA_MATER     1
returns_73_PER_EMP. SIDERURGICA_MATER    1
returns_74_PER_CASA GRANDE_CONS. BAS     1
returns_75_PER_TREVALI MINING_MATER      1
Length: 75, dtype: int64
Correccion
Nas: returns_1_CHL_AGUAS_SERV. P              0
returns_2_CHL_ANDINA_CONS. BAS           0
returns_3_CHL_ANTAR_ENER                 0
returns_4_CHL_BANCO CREDITO_FINAN        0
returns_5_CHL_BANCO STDER_FINAN          0
                                        ..
returns_71_PER_FERREYROS_INDUST          0
returns_72_PER_ACEROS AREQUIPA_MATER     0
returns_73_PER_EMP. SIDERURGICA_MATER    0
returns_74_PER_CASA GRANDE_CONS. BAS     0
returns_75_PER_TREVALI MINING_MATER      0
Length: 

d:\AnalisisAcciones\acciones\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: An unsupported index was provided and will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
d:\AnalisisAcciones\acciones\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: An unsupported index was provided and will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
d:\AnalisisAcciones\acciones\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: An unsupported index was provided and will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
d:\AnalisisAcciones\acciones\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: An unsupported index was provided and will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
d:\AnalisisAcciones\acciones\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: An unsupported index was provided and will be ignored when e.g. 

termine modelos
aic:  18
aic:  19
aic:  17
aic:  18
aic:  18
aic:  17
aic:  18
aic:  19
aic:  18
aic:  18
aic:  17
aic:  19
aic:  19
aic:  17
aic:  17
aic:  17
aic:  18
aic:  19
aic:  19
aic:  19
aic:  19
aic:  19
aic:  19
aic:  17
aic:  18
aic:  17
aic:  20
aic:  17
aic:  17
aic:  19
aic:  17
aic:  17
aic:  19
aic:  20
aic:  17
aic:  17
aic:  19
aic:  20
aic:  17
aic:  19
aic:  20
aic:  15
aic:  17
aic:  17
aic:  18
aic:  19
aic:  18
aic:  19
aic:  18
aic:  12
aic:  18
aic:  19
aic:  20
aic:  18
aic:  12
aic:  19
aic:  20
aic:  17
aic:  14
aic:  12
aic:  14
aic:  19
aic:  19
aic:  19
aic:  19
aic:  19
aic:  20
aic:  12
aic:  18
aic:  19
aic:  20
aic:  12
aic:  20
aic:  19
aic:  12
aic:  12
aic:  19
aic:  19
aic:  20
aic:  12
aic:  13
aic:  12
aic:  12
aic:  20
aic:  20
aic:  13
aic:  17
aic:  17
aic:  18
aic:  18
aic:  17
aic:  18
aic:  18
aic:  20
aic:  18
aic:  18
aic:  18
aic:  19
aic:  17
aic:  20
aic:  20
aic:  15
aic:  17
aic:  12
aic:  18
aic:  20
aic:  20
aic:  20
aic:  20
aic

d:\AnalisisAcciones\acciones\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: An unsupported index was provided and will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
d:\AnalisisAcciones\acciones\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: An unsupported index was provided and will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
d:\AnalisisAcciones\acciones\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: An unsupported index was provided and will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
d:\AnalisisAcciones\acciones\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: An unsupported index was provided and will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
d:\AnalisisAcciones\acciones\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: An unsupported index was provided and will be ignored when e.g. 

(3986, 2)
collinearity_var1    0
collinearity_var2    0
dtype: int64


In [ ]:
df_test = test_results.copy()

In [ ]:
stocks_porfolio_1 = Portafolio.clean_output_model(df_test)

In [ ]:
a = Portafolio.results.test_causality(caused="returns_1_CHL_AGUAS_SERV. P",causing="returns_32_COL_BANCOLOMBIA_FINAN")

In [ ]:
prueba = df_transform[["returns_1_CHL_AGUAS_SERV. P","returns_32_COL_BANCOLOMBIA_FINAN"]]
models_results_by_lags = {}
model = VAR(prueba)
max_lag = 21

for i in np.arange(1,max_lag):
    result = model.fit(i)
    models_results_by_lags[i] = {"AIC":result.aic,
                        "BIC":result.bic,
                        'FPE': result.fpe,
                        'HQIC':result.hqic}


def iter_var(criterio,max_lag):
    salida = [abs(models_results_by_lags[id][criterio]) for id in np.arange(1,max_lag)]
    max_lag = salida.index(min(salida))+1
    print(f"{criterio}: ",max_lag)
    return max_lag

list_AIC = iter_var("AIC",max_lag)
list_BIC = iter_var("BIC",max_lag)
list_FPE = iter_var("FPE",max_lag)
list_HQIC = iter_var("HQIC",max_lag)

print(list_BIC<=list_HQIC<=list_AIC)

results = model.fit(maxlags=6, ic='fpe')

In [ ]:
df = df_transform[["returns_1_CHL_AGUAS_SERV. P","returns_44_MEX_BIMBO_CONS. BAS"]]

In [ ]:
Portafolio.apply_vif(df)